# ตัวแทน AutoGen ในการใช้งานจริง: การสังเกตการณ์และการประเมินผล

ในบทเรียนนี้ เราจะเรียนรู้วิธี **ติดตามขั้นตอนภายใน (traces) ของ [ตัวแทน Autogen](https://github.com/microsoft/autogen)** และ **ประเมินประสิทธิภาพ** โดยใช้ [Langfuse](https://langfuse.com)

คู่มือนี้ครอบคลุมถึงตัวชี้วัดการประเมินผลทั้งแบบ **ออนไลน์** และ **ออฟไลน์** ที่ทีมงานใช้เพื่อนำตัวแทนเข้าสู่การใช้งานจริงได้อย่างรวดเร็วและน่าเชื่อถือ

**ทำไมการประเมินตัวแทน AI ถึงสำคัญ:**
- แก้ไขปัญหาเมื่อภารกิจล้มเหลวหรือให้ผลลัพธ์ที่ไม่เหมาะสม
- ติดตามค่าใช้จ่ายและประสิทธิภาพแบบเรียลไทม์
- เพิ่มความน่าเชื่อถือและความปลอดภัยผ่านการให้ข้อเสนอแนะอย่างต่อเนื่อง


## ขั้นตอนที่ 1: ตั้งค่าตัวแปรสภาพแวดล้อม

รับคีย์ API ของ Langfuse โดยการสมัครใช้งาน [Langfuse Cloud](https://cloud.langfuse.com/) หรือ [โฮสต์ Langfuse ด้วยตัวเอง](https://langfuse.com/self-hosting)

_**หมายเหตุ:** ผู้ที่โฮสต์ด้วยตัวเองสามารถใช้ [โมดูล Terraform](https://langfuse.com/self-hosting/azure) เพื่อปรับใช้ Langfuse บน Azure หรือเลือกปรับใช้ Langfuse บน Kubernetes โดยใช้ [Helm chart](https://langfuse.com/self-hosting/kubernetes-helm)_


In [5]:
import os

# Get keys for your project from the project settings page: https://cloud.langfuse.com
os.environ["LANGFUSE_PUBLIC_KEY"] = "pk-lf-..." 
os.environ["LANGFUSE_SECRET_KEY"] = "sk-lf-..." 
os.environ["LANGFUSE_HOST"] = "https://cloud.langfuse.com" # 🇪🇺 EU region
# os.environ["LANGFUSE_HOST"] = "https://us.cloud.langfuse.com" # 🇺🇸 US region

ด้วยตัวแปรสภาพแวดล้อมที่ตั้งค่าไว้ เราสามารถเริ่มต้นไคลเอนต์ Langfuse ได้แล้ว `get_client()` จะเริ่มต้นไคลเอนต์ Langfuse โดยใช้ข้อมูลรับรองที่ระบุไว้ในตัวแปรสภาพแวดล้อม


In [6]:
from langfuse import Langfuse
 
# Filter out Autogen OpenTelemetryspans
langfuse = Langfuse(
    blocked_instrumentation_scopes=["autogen SingleThreadedAgentRuntime"]
)
 
# Verify connection
if langfuse.auth_check():
    print("Langfuse client is authenticated and ready!")
else:
    print("Authentication failed. Please check your credentials and host.")

Langfuse client is authenticated and ready!


## ขั้นตอนที่ 2: เริ่มต้นการใช้งาน OpenLit Instrumentation

ตอนนี้เราจะเริ่มต้นการใช้งาน [OpenLit](https://github.com/openlit/openlit) instrumentation ซึ่ง OpenLit จะทำการจับการทำงานของ AutoGen โดยอัตโนมัติและส่งออก OpenTelemetry (OTel) spans ไปยัง Langfuse


In [7]:
import openlit
 
# Initialize OpenLIT instrumentation. The disable_batch flag is set to true to process traces immediately.
openlit.init(tracer=langfuse._otel_tracer, disable_batch=True, disabled_instrumentors=["mistral"])

## ขั้นตอนที่ 3: เรียกใช้งานตัวแทนของคุณ

ตอนนี้เราจะตั้งค่าตัวแทนแบบหลายรอบเพื่อทดสอบการติดตั้งเครื่องมือของเรา


In [2]:
import os

from autogen_agentchat.agents import AssistantAgent
from autogen_ext.models.azure import AzureAIChatCompletionClient
from azure.core.credentials import AzureKeyCredential
from autogen_agentchat.base import TaskResult

from autogen_agentchat.conditions import TextMentionTermination
from autogen_agentchat.teams import RoundRobinGroupChat

In [3]:
client = AzureAIChatCompletionClient(
    model="gpt-4o-mini",
    endpoint="https://models.inference.ai.azure.com",
    # To authenticate with the model you will need to generate a personal access token (PAT) in your GitHub settings.
    # Create your PAT token by following instructions here: https://docs.github.com/en/authentication/keeping-your-account-and-data-secure/managing-your-personal-access-tokens
    credential=AzureKeyCredential(os.environ["GITHUB_TOKEN"]),
    model_info={
        "json_output": True,
        "function_calling": True,
        "vision": True,
        "family": "unknown",
        "structured_output": False
    },
)

In [8]:
# 🍴 Agent 1 – proposes ONE healthy meal idea each turn
meal_planner_agent = AssistantAgent(
    "meal_planner_agent",
    model_client=client,
    description="A seasoned meal-planning coach who suggests balanced meals.",
    system_message="""
    You are a Meal-Planning Assistant with a decade of experience helping busy people prepare meals.
    Goal: propose the single best meal (breakfast, lunch, or dinner) given the user's context.
    Each response must contain ONLY one complete meal idea (title + very brief component list) — no extras.
    Keep it concise: skip greetings, chit-chat, and filler.
    """,
)

# 🥗 Agent 2 – checks nutritional quality & variety
nutritionist_agent = AssistantAgent(
    "nutritionist_agent",
    model_client=client,
    description="A registered dietitian ensuring meals meet nutritional standards.",
    system_message="""
    You are a Nutritionist focused on whole-food, macro-balanced eating.
    Evaluate the meal_planner_agent’s recommendation.
    If the meal is nutritionally sound, sufficiently varied, and portion-appropriate, respond with 'APPROVE'.
    Otherwise, give high-level guidance on how to improve it (e.g. 'add a plant-based protein') — do NOT provide a full alternative recipe.
    """,
)

In [9]:
# ✅ Chat stops once the nutritionist says APPROVE
termination = TextMentionTermination("APPROVE")

# 🔄 Alternate turns between the two agents until termination
team = RoundRobinGroupChat(
    [meal_planner_agent, nutritionist_agent],
    termination_condition=termination,
)

# Example kickoff
user_input = "I'm looking for a quick, delicious dinner I can prep after work. I have 30 minutes and minimal clean-up is ideal."

In [ ]:
with langfuse.start_as_current_span(name="create_meal_plan") as span:
    async for message in team.run_stream(task=user_input):
        if isinstance(message, TaskResult):
            print("Stop Reason:", message.stop_reason)
        else:
            print(message)

    span.update_trace(
        input=user_input,
        output=message.stop_reason,
    )

# Flush the trace to Langfuse for short-lived environments such as Jupyter Notebooks
langfuse.flush()

### โครงสร้าง Trace

Langfuse บันทึก **trace** ซึ่งประกอบด้วย **spans** ที่แสดงถึงแต่ละขั้นตอนของตรรกะของเอเจนต์ของคุณ ในที่นี้ trace ประกอบด้วยการทำงานโดยรวมของเอเจนต์และ sub-spans สำหรับ:
- เอเจนต์วางแผนมื้ออาหาร
- เอเจนต์นักโภชนาการ

คุณสามารถตรวจสอบสิ่งเหล่านี้เพื่อดูได้อย่างชัดเจนว่าเวลาใช้ไปที่ไหน จำนวนโทเค็นที่ใช้ และอื่น ๆ:

![แผนผัง Trace ใน Langfuse](https://langfuse.com/images/cookbook/example-autogen-evaluation/trace-tree.png)

_[ลิงก์ไปยัง trace](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64)_


## การประเมินผลออนไลน์

การประเมินผลออนไลน์หมายถึงการประเมินตัวแทนในสภาพแวดล้อมจริงแบบสด นั่นคือระหว่างการใช้งานจริงในระบบผลิต ซึ่งเกี่ยวข้องกับการติดตามประสิทธิภาพของตัวแทนในปฏิสัมพันธ์กับผู้ใช้จริงและการวิเคราะห์ผลลัพธ์อย่างต่อเนื่อง

### ตัวชี้วัดทั่วไปที่ควรติดตามในระบบผลิต

1. **ค่าใช้จ่าย** — การวัดผลจะจับการใช้งานโทเค็น ซึ่งคุณสามารถแปลงเป็นค่าใช้จ่ายโดยประมาณได้โดยกำหนดราคาต่อโทเค็น
2. **ความล่าช้า** — สังเกตเวลาที่ใช้ในการดำเนินการแต่ละขั้นตอน หรือการดำเนินการทั้งหมด
3. **ความคิดเห็นจากผู้ใช้** — ผู้ใช้สามารถให้ความคิดเห็นโดยตรง (เช่น กดถูกใจ/ไม่ถูกใจ) เพื่อช่วยปรับปรุงหรือแก้ไขตัวแทน
4. **LLM-as-a-Judge** — ใช้ LLM แยกต่างหากเพื่อประเมินผลลัพธ์ของตัวแทนในเวลาใกล้เคียงกับเรียลไทม์ (เช่น การตรวจสอบความเหมาะสมหรือความถูกต้อง)

ด้านล่างนี้เป็นตัวอย่างของตัวชี้วัดเหล่านี้


#### 1. ค่าใช้จ่าย

ด้านล่างนี้เป็นภาพหน้าจอที่แสดงการใช้งานสำหรับการเรียก `gpt-4o-mini` ซึ่งมีประโยชน์ในการดูขั้นตอนที่มีค่าใช้จ่ายสูงและปรับปรุงประสิทธิภาพของตัวแทนของคุณ

![Costs](https://langfuse.com/images/cookbook/example-autogen-evaluation/gpt-4o-costs.png) 

_[ลิงก์ไปยังการติดตาม](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64)_


#### 2. ความหน่วงเวลา

เรายังสามารถดูได้ว่าแต่ละขั้นตอนใช้เวลานานเท่าใด ในตัวอย่างด้านล่าง การดำเนินการทั้งหมดใช้เวลาประมาณ 3 วินาที ซึ่งสามารถแยกย่อยตามขั้นตอนได้ สิ่งนี้ช่วยให้คุณระบุจุดที่เป็นคอขวดและปรับปรุงประสิทธิภาพของตัวแทนได้

![Latency](https://langfuse.com/images/cookbook/example-autogen-evaluation/agent-latency.png) 

_[Link to the trace](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64?display=timeline)_


#### 3. ข้อเสนอแนะจากผู้ใช้

หากตัวแทนของคุณถูกฝังอยู่ในส่วนติดต่อผู้ใช้ คุณสามารถบันทึกข้อเสนอแนะโดยตรงจากผู้ใช้ (เช่น การกดถูกใจ/ไม่ถูกใจในส่วนติดต่อการแชท)


In [10]:
from langfuse import get_client
 
langfuse = get_client()
 
# Option 1: Use the yielded span object from the context manager
with langfuse.start_as_current_span(
    name="autogen-request-user-feedback-1") as span:
    
    async for message in team.run_stream(task="Create a meal with potatoes"):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message)    
 
    # Score using the span object
    span.score_trace(
        name="user-feedback",
        value=1,
        data_type="NUMERIC",
        comment="This was delicious, thank you"
    )
 
# Option 2: Use langfuse.score_current_trace() if still in context
with langfuse.start_as_current_span(name="autogen-request-user-feedback-2") as span:
    # ... Autogen execution ...

    async for message in team.run_stream(task="I am allergic to gluten."):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message)    
 
    # Score using current context
    langfuse.score_current_trace(
        name="user-feedback",
        value=1,
        data_type="NUMERIC"
    )

id='da068880-22ae-4f01-9f01-2bb231939089' source='user' models_usage=None metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 43, 732669, tzinfo=datetime.timezone.utc) content='Create a meal with potatoes' type='TextMessage'
id='ad937ce4-3534-493f-824b-ca9c226b5287' source='meal_planner_agent' models_usage=RequestUsage(prompt_tokens=95, completion_tokens=30) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 45, 186423, tzinfo=datetime.timezone.utc) content='Potato and Spinach Frittata  \n- Eggs  \n- Potatoes  \n- Fresh spinach  \n- Onion  \n- Cheese (optional)  ' type='TextMessage'
id='50fd33c1-057f-49fe-afad-ee86d164296d' source='nutritionist_agent' models_usage=RequestUsage(prompt_tokens=132, completion_tokens=4) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 45, 581059, tzinfo=datetime.timezone.utc) content='APPROVE' type='TextMessage'
Stop Reason: Text 'APPROVE' mentioned
id='e371de6c-e5fc-42c1-8eda-e5b8cd5accab' source='user' models_usage=None met

In [ ]:
# Option 3: Use create_score() with trace ID (when outside context)
langfuse.create_score(
    trace_id="predefined_trace_id",
    name="user-feedback",
    value=1,
    data_type="NUMERIC",
    comment="This was correct, thank you"
)

การตอบกลับจากผู้ใช้งานจะถูกบันทึกใน Langfuse:

![การตอบกลับจากผู้ใช้งานกำลังถูกบันทึกใน Langfuse](https://langfuse.com/images/cookbook/example-autogen-evaluation/user-feedback.png)


#### 4. การให้คะแนนแบบอัตโนมัติด้วย LLM-as-a-Judge

LLM-as-a-Judge เป็นอีกวิธีหนึ่งในการประเมินผลลัพธ์ของเอเจนต์ของคุณโดยอัตโนมัติ คุณสามารถตั้งค่าการเรียก LLM แยกต่างหากเพื่อวัดความถูกต้อง ความเป็นพิษ สไตล์ หรือเกณฑ์อื่น ๆ ที่คุณสนใจ

**ขั้นตอนการทำงาน**:
1. คุณกำหนด **เทมเพลตการประเมินผล** เช่น "ตรวจสอบว่าข้อความมีความเป็นพิษหรือไม่"
2. คุณตั้งค่ารุ่นที่ใช้เป็น judge-model; ในกรณีนี้คือ `gpt-4o-mini` ที่เรียกผ่าน Azure
3. ทุกครั้งที่เอเจนต์ของคุณสร้างผลลัพธ์ คุณจะส่งผลลัพธ์นั้นไปยัง LLM "ผู้ตัดสิน" พร้อมกับเทมเพลต
4. LLM ผู้ตัดสินจะตอบกลับด้วยคะแนนหรือป้ายกำกับที่คุณบันทึกลงในเครื่องมือสังเกตการณ์ของคุณ

ตัวอย่างจาก Langfuse:

![LLM-as-a-Judge Evaluator](https://langfuse.com/images/cookbook/example-autogen-evaluation/evaluator.png)


In [12]:
with langfuse.start_as_current_span(name="autogen-request-user-feedback-2") as span:

    async for message in team.run_stream(task="I am a picky eater and not sure if you find something for me."):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message) 

    span.update_trace(
        input=user_input,
        output=message.stop_reason,
    )

langfuse.flush()

id='eefc628d-502f-451a-8f70-be486f62f8c5' source='user' models_usage=None metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 29, 171393, tzinfo=datetime.timezone.utc) content='I am a picky eater and not sure if you find something for me.' type='TextMessage'
id='13b3e14b-bcf7-42a5-80d6-54b0c7be765e' source='meal_planner_agent' models_usage=RequestUsage(prompt_tokens=352, completion_tokens=27) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 30, 433516, tzinfo=datetime.timezone.utc) content='Chicken Alfredo Pasta  \n- Gluten-free pasta  \n- Grilled chicken breast  \n- Heavy cream  \n- Parmesan cheese  \n- Garlic  ' type='TextMessage'
id='550f2dee-0e08-4bbd-b67f-991b467328f1' source='nutritionist_agent' models_usage=RequestUsage(prompt_tokens=386, completion_tokens=17) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 31, 505173, tzinfo=datetime.timezone.utc) content='Consider incorporating some vegetables, like spinach or broccoli, to increase the nutrien

คุณสามารถเห็นได้ว่าคำตอบของตัวอย่างนี้ถูกตัดสินว่า "ไม่เป็นพิษ"

![LLM-as-a-Judge Evaluation Score](https://langfuse.com/images/cookbook/example-autogen-evaluation/llm-as-a-judge-score.png)


#### 5. ภาพรวมของตัวชี้วัดการสังเกตการณ์

ตัวชี้วัดทั้งหมดนี้สามารถแสดงผลร่วมกันในแดชบอร์ดได้ ซึ่งช่วยให้คุณสามารถดูประสิทธิภาพของตัวแทนในหลายเซสชันได้อย่างรวดเร็ว และช่วยติดตามตัวชี้วัดคุณภาพในระยะยาว


## การประเมินผลแบบออฟไลน์

การประเมินผลแบบออนไลน์มีความสำคัญสำหรับการรับความคิดเห็นแบบเรียลไทม์ แต่คุณยังต้องการ **การประเมินผลแบบออฟไลน์**—การตรวจสอบอย่างเป็นระบบก่อนหรือระหว่างการพัฒนา สิ่งนี้ช่วยรักษาคุณภาพและความน่าเชื่อถือก่อนที่จะนำการเปลี่ยนแปลงเข้าสู่การใช้งานจริง


### การประเมินชุดข้อมูล

ในการประเมินแบบออฟไลน์ คุณมักจะ:
1. มีชุดข้อมูลมาตรฐาน (ที่มีคู่ของคำถามและคำตอบที่คาดหวัง)
2. รันตัวแทนของคุณบนชุดข้อมูลนั้น
3. เปรียบเทียบผลลัพธ์กับผลลัพธ์ที่คาดหวัง หรือใช้กลไกการให้คะแนนเพิ่มเติม

ด้านล่างนี้ เราแสดงวิธีการนี้ด้วย [q&a-dataset](https://huggingface.co/datasets/junzhang1207/search-dataset) ซึ่งประกอบด้วยคำถามและคำตอบที่คาดหวัง


In [16]:
import pandas as pd
from datasets import load_dataset
 
# Fetch search-dataset from Hugging Face
dataset = load_dataset("junzhang1207/search-dataset", split = "train")
df = pd.DataFrame(dataset)
print("First few rows of search-dataset:")
print(df.head())

/Users/jannik/Documents/GitHub/ai-agents-for-beginners/.venv/lib/python3.13/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


First few rows of search-dataset:
                                     id  \
0  20caf138-0c81-4ef9-be60-fe919e0d68d4   
1  1f37d9fd-1bcc-4f79-b004-bc0e1e944033   
2  76173a7f-d645-4e3e-8e0d-cca139e00ebe   
3  5f5ef4ca-91fe-4610-a8a9-e15b12e3c803   
4  64dbed0d-d91b-4acd-9a9c-0a7aa83115ec   

                                            question  \
0                 steve jobs statue location budapst   
1  Why is the Battle of Stalingrad considered a t...   
2  In what year did 'The Birth of a Nation' surpa...   
3  How many Russian soldiers surrendered to AFU i...   
4   What event led to the creation of Google Images?   

                                     expected_answer       category       area  
0  The Steve Jobs statue is located in Budapest, ...           Arts  Knowledge  
1  The Battle of Stalingrad is considered a turni...   General News       News  
2  This question is based on a false premise. 'Th...  Entertainment       News  
3  About 300 Russian soldiers surrendered to t

ต่อไป เราสร้างเอนทิตีชุดข้อมูลใน Langfuse เพื่อติดตามการทำงาน จากนั้นเราเพิ่มแต่ละรายการจากชุดข้อมูลลงในระบบ


In [17]:
from langfuse import Langfuse
langfuse = Langfuse()
 
langfuse_dataset_name = "qa-dataset_autogen-agent"
 
# Create a dataset in Langfuse
langfuse.create_dataset(
    name=langfuse_dataset_name,
    description="q&a dataset uploaded from Hugging Face",
    metadata={
        "date": "2025-03-21",
        "type": "benchmark"
    }
)

Dataset(id='cmcm7524d00kjad07s2cjwqcf', name='qa-dataset_autogen-agent', description='q&a dataset uploaded from Hugging Face', metadata={'date': '2025-03-21', 'type': 'benchmark'}, project_id='cloramnkj0002jz088vzn1ja4', created_at=datetime.datetime(2025, 7, 2, 16, 54, 7, 357000, tzinfo=datetime.timezone.utc), updated_at=datetime.datetime(2025, 7, 2, 16, 54, 7, 357000, tzinfo=datetime.timezone.utc))

In [18]:
df_25 = df.sample(25) # For this example, we upload only 25 dataset questions

for idx, row in df_25.iterrows():
    langfuse.create_dataset_item(
        dataset_name=langfuse_dataset_name,
        input={"text": row["question"]},
        expected_output={"text": row["expected_answer"]}
    )

![รายการชุดข้อมูลใน Langfuse](https://langfuse.com/images/cookbook/example-autogen-evaluation/example-dataset.png)


#### การรัน Agent บน Dataset

ก่อนอื่น เราจะสร้าง Autogen agent แบบง่าย ๆ ที่ตอบคำถามโดยใช้โมเดล Azure OpenAI


In [8]:
import os
from dotenv import load_dotenv

from autogen_agentchat.agents import AssistantAgent
from autogen_core.models import UserMessage
from autogen_ext.models.azure import AzureAIChatCompletionClient
from azure.core.credentials import AzureKeyCredential
from autogen_core import CancellationToken
from autogen_agentchat.messages import TextMessage

In [ ]:
load_dotenv()
client = AzureAIChatCompletionClient(
    model="gpt-4o",
    endpoint="https://models.inference.ai.azure.com",
    # To authenticate with the model you will need to generate a personal access token (PAT) in your GitHub settings.
    # Create your PAT token by following instructions here: https://docs.github.com/en/authentication/keeping-your-account-and-data-secure/managing-your-personal-access-tokens
    credential=AzureKeyCredential(os.getenv("GITHUB_TOKEN")),
    max_tokens=5000,
    model_info={
        "json_output": True,
        "function_calling": False,
        "vision": False,
        "family": "unknown",
        "structured_output": True,
    },
)

result = await client.create([UserMessage(content="What is the capital of France?", source="user")])
print(result)

In [18]:
agent = AssistantAgent(
    name="assistant",
    model_client=client,
    tools=[],
    system_message="You are participant in a quizz show and you are given a question. You need to create a short answer to the question.",
)

จากนั้น เรากำหนดฟังก์ชันตัวช่วย `my_agent()`


In [19]:
async def my_agent(user_query: str):

    with langfuse.start_as_current_span(name="autogen-trace") as span:

        # Execute the agent response
        response = await agent.on_messages(
            [TextMessage(content=user_query, source="user")],
            cancellation_token=CancellationToken(),
        )

        span.update_trace(
            input=user_query,
            output=response.chat_message.content,
        )

    return str(response.chat_message.content)

# Test the function
await my_agent("What is the capital of France?")

'The capital of France is Paris.'

ในที่สุด เราทำการวนซ้ำผ่านแต่ละรายการในชุดข้อมูล เรียกใช้งานตัวแทน และเชื่อมโยงร่องรอยกับรายการในชุดข้อมูล เราสามารถแนบคะแนนการประเมินอย่างรวดเร็วได้หากต้องการ


In [20]:
dataset_name = "qa-dataset_autogen-agent"
current_run_name = "dev_tasks_run-autogen_gpt-4.1" # Identifies this specific evaluation run
current_run_metadata={"model_provider": "Azure", "model": "gpt-4.1"}
current_run_description="Evaluation run for Autogen model on July 3rd"

dataset = langfuse.get_dataset('qa-dataset_autogen-agent')

for item in dataset.items:
    print(f"Running evaluation for item: {item.id} (Input: {item.input})")
 
    # Use the item.run() context manager
    with item.run(
        run_name=current_run_name,
        run_metadata=current_run_metadata,
        run_description=current_run_description
    ) as root_span: 
        # All subsequent langfuse operations within this block are part of this trace.
        generated_answer = await my_agent(user_query = item.input["text"])
    
    print("Generated Answer: ", generated_answer)
 
print(f"\nFinished processing dataset '{dataset_name}' for run '{current_run_name}'.")

langfuse.flush()

Running evaluation for item: 09810cc4-9992-4712-a3b2-7224da31776a (Input: {'text': 'In Hindu mythology, which deity is the Ganges river dolphin associated with?'})
Generated Answer:  In Hindu mythology, the Ganges river dolphin is associated with the deity Ganga.
Running evaluation for item: bb113f94-7723-47c6-8c34-59d883044514 (Input: {'text': 'What significant discovery did the LHCb collaboration report in 2015?'})
Generated Answer:  In 2015, the LHCb collaboration reported the discovery of pentaquark particles.
Running evaluation for item: 4d8ae54e-ceab-46d0-ad2c-6e8e223589a9 (Input: {'text': 'What is the MÄ\x81ori name for the red-crowned parakeet?'})
Generated Answer:  The Māori name for the red-crowned parakeet is kākāriki.
Running evaluation for item: 21e5a0d5-f619-4a73-868e-9955053b3e72 (Input: {'text': 'Who starred in the 1978 television film adaptation of Les MisÃ©rables?'})
Generated Answer:  Richard Jordan starred as Jean Valjean in the 1978 television film adaptation of Le

คุณสามารถทำกระบวนการนี้ซ้ำได้ด้วยการตั้งค่าตัวแทนที่แตกต่างกัน เช่น:
- โมเดล (gpt-4o-mini, gpt-4.1, เป็นต้น)
- คำสั่ง (prompts)
- เครื่องมือ (ค้นหากับไม่ค้นหา)
- ความซับซ้อนของตัวแทน (ตัวแทนหลายตัวเทียบกับตัวแทนเดี่ยว)

จากนั้นเปรียบเทียบผลลัพธ์แบบเคียงข้างกันใน Langfuse ในตัวอย่างนี้ ฉันได้รันตัวแทน 3 ครั้งในคำถามชุดข้อมูล 25 ข้อ สำหรับแต่ละการรัน ฉันใช้โมเดล Azure OpenAI ที่แตกต่างกัน คุณจะเห็นว่าจำนวนคำถามที่ตอบถูกต้องเพิ่มขึ้นเมื่อใช้โมเดลที่ใหญ่ขึ้น (ตามที่คาดไว้) คะแนน `correct_answer` ถูกสร้างขึ้นโดย [LLM-as-a-Judge Evaluator](https://langfuse.com/docs/scores/model-based-evals) ซึ่งถูกตั้งค่าให้ประเมินความถูกต้องของคำถามโดยอ้างอิงจากคำตอบตัวอย่างที่ให้ไว้ในชุดข้อมูล

![ภาพรวมการรันชุดข้อมูล](https://langfuse.com/images/cookbook/example-autogen-evaluation/dataset_runs.png)
![การเปรียบเทียบการรันชุดข้อมูล](https://langfuse.com/images/cookbook/example-autogen-evaluation/dataset-run-comparison.png)



---

**ข้อจำกัดความรับผิดชอบ**:  
เอกสารนี้ได้รับการแปลโดยใช้บริการแปลภาษา AI [Co-op Translator](https://github.com/Azure/co-op-translator) แม้ว่าเราจะพยายามให้การแปลมีความถูกต้องมากที่สุด แต่โปรดทราบว่าการแปลโดยอัตโนมัติอาจมีข้อผิดพลาดหรือความไม่ถูกต้อง เอกสารต้นฉบับในภาษาดั้งเดิมควรถือเป็นแหล่งข้อมูลที่เชื่อถือได้ สำหรับข้อมูลที่สำคัญ ขอแนะนำให้ใช้บริการแปลภาษามืออาชีพ เราไม่รับผิดชอบต่อความเข้าใจผิดหรือการตีความผิดที่เกิดจากการใช้การแปลนี้
